# 0184934-付子乾 —— 提取金融学院所有老师信息

In [25]:
import re
import requests
from lxml import etree
import pandas

global headers
headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:82.0) Gecko/20100101 Firefox/82.0'}
total_url = 'http://finance.jxufe.edu.cn/news-list-shuodao-{}.html'      # 金融学院硕导首页界面
r_text = requests.get(total_url.format(1), headers=headers).text         # 首取第一页
html = etree.HTML(r_text)

### 提取硕导界面一共有多少页

In [26]:
# 提取硕导界面一共有多少页
num = html.xpath('//div[@class="bd_listabc"]//p/span[@class="num"]/text()')[0]
print(num)
page_num = int(re.findall(r".+/(\d)页", num, re.DOTALL)[0])
print(page_num)

共32条记录　1/3页
3


### 翻页，同时获得每个老师的url

In [27]:
# 翻页，同时获得每个老师的url
for i in range(1, page_num+1):
    # 因为之前取页码的时候用是售页，所有不需要再爬取，因此有如下判断
    if i >= 2:
        r_text = requests.get(total_url.format(i), headers=headers).text
        html = etree.HTML(r_text)
    # 观察易知，每个老师的url位于class属性为bd_listabc，子目录的a的href属性中，具体如下
    urls = html.xpath('//div[@class="bd_listabc"]//li//div[@class="textlist"]/a/@href')

print(urls)    # 打印输出页面的url，这里以最后一页为例
        

['http://finance.jxufe.edu.cn/news-show-2065.html', 'http://finance.jxufe.edu.cn/news-show-2847.html', 'http://finance.jxufe.edu.cn/news-show-1321.html', 'http://finance.jxufe.edu.cn/news-show-1322.html', 'http://finance.jxufe.edu.cn/news-show-1320.html', 'http://finance.jxufe.edu.cn/news-show-1317.html', 'http://finance.jxufe.edu.cn/news-show-1318.html', 'http://finance.jxufe.edu.cn/news-show-3349.html']


## 每个老师信息的处理

### 变量准备

In [28]:
# 每个老师信息的处理，变量准备(这里随便取了一个老师为例子)
# 经观察，所有老师的信息都存在在一个class属性为ne_main_R的div标签内
r = requests.get(urls[1], headers=headers).text
html = etree.HTML(r)
target = html.xpath('//div[@class="ne_main_R"]//p')  # 所有p标签下内容
div_text = html.xpath('//div[@class="ne_main_R"]//div[@class="jianjie_c"]/text()')   # 所有div标签下内容
div_span_text = html.xpath('//div[@class="ne_main_R"]//div[@class="jianjie_c"]//span/text()')  # 所有div标签内的span标签内容
Flag = 0    # 不同情况下的标识处理
symbol = '：'   # 由于硕导老师中存在外教，其负号会存在不同，因此定义symbol变量
info = []
infos = []
Basic_info = {}
# 下列的两个变量都是为了使不同老师的dict有相同的key，而需要准备的转化变量
sub_info = ['职务','职称','联系方式','毕业专业','最高学历','政治面貌','毕业院校','出生年月']   
sub_dict = {'Name':'姓名','Sex':'性别','Graduated':'毕业院校','Duties':'职务',
                'Email':'联系方式', 'Jobtitle':'职称','邮箱':'联系方式','电子邮箱':'联系方式'}
     
# xpath的element类型示例
print(target[1:5])

[<Element p at 0x1ff4af93e48>, <Element p at 0x1ff4af93fc8>, <Element p at 0x1ff4aae4448>, <Element p at 0x1ff4aae4688>]


### 信息提取与处理

In [29]:
# 对上述p标签进行循环处理
from IPython.display import display, HTML
import pandas as pd
for i in range(len(target)):
    tar = target[i]
    # 基本信息
    content1 = tar.xpath('.//strong/text()')
    content2 = tar.xpath('.//span/text()')
    content3 = tar.xpath('./text()')
    content = content1 + content2 + content3
    # Flag = 0 表示对基本信息的提取；依次递推1表示对个人简介的提取，2表示对研究成果的提取
    if Flag == 0:
        # 经过多次更改标签形式的爬取结果可知，所有老师的基本信息都位于上述3个Content的标签下
        # 具有一定的规则性，因此考虑对其细分
        # 由于得到的content是个列表，需要根据情况对其进行处理
        # 有些老师的内容分散在不同的标签下，因此content列表的大小对应着不同情况
        if len(content) == 0:
            continue

        # 三个以上
        # 例：['姓名', '：', 'xxx']或['毕业','院校', ':xx', 'xxx']
        elif len(content) > 2:
            # 列表转字符方便后续正则处理
            content = ''.join(content)
            if symbol == content[-1]:
                # 这里的相加顺序是均具备这个规则，一般
                content = content1 + content3 + content2

            content = ''.join(content)
            # 以分号(全角或半角状态)为分隔标识，用正则匹配结果
            # 注：该处起，content1指的是如姓名、性别这种关键词key，而content2指的是对应的内容value
            try:
                content1 = re.findall(r"(.+){}".format(symbol), content, re.DOTALL)[0]
                content2 = re.findall(r"{}(.+)".format(symbol), content, re.DOTALL)[0]
            except:
                print('ERROR',content)
        # 有两个
        # 例：['姓名：', 'xxx']或['毕业院校', ':xxxxx']
        elif len(content) == 2:
            content1 = content[0]
            content2 = content[1]
        #只有一个
        else:
            # \uxxx类型的出现
            try:
                content1 = re.findall(r"(.+){}".format(symbol), content[0], re.DOTALL)
            except:
                continue
            # 空Key
            if len(content1) == 0:
                continue
            content1 = content1[0]
            try:
                content2 = re.findall(r"{}(.+)".format(symbol), content[0], re.DOTALL)[0]
            except:
                print('!Error', content1)
        ## 相对之前的操作，这里换掉了json，直接用replace替换掉无关文本
        content1 = content1.replace('\u3000','').replace('\u200b','').replace('\xa0','')
        content2 = content2.replace('\u3000','').replace('\u200b','').replace('\xa0','')

        if symbol in content1:
            content1 = (content1.replace(' ', ''))[:-1]

        if symbol in content2:
            content2 = (content2.replace(' ', ''))[1:]
            if content2 == '':
                content2 = '无'
                
        # 联系方式(邮箱)转化成一样的key，以及对外教老师的转化处理
        if re.match(r'[a-zA-Z]+', content1) or re.match(r'邮箱', content1.replace(' ','')):
            content1 = sub_dict[content1.replace(' ','')]
   
        Basic_info[content1.replace(' ','')] = [content2]
        # 联系方式，邮箱，职称
        if i >= 5:
            string = str(Basic_info.keys())
            if ('联系方式' in list(Basic_info.keys())[-1] and '称' in string) or ('箱' in list(Basic_info.keys())[-1] and '称' in string) or ('邮&nbsp' not in r and '联系方式' not in r and '称' in list(Basic_info.keys())[-1]):
                Flag = 1
            if ('Email' in string and 'Duties' in string):
                Flag = 1
    # 自我简介
    elif Flag == 1:
        # 由于自我简介以及科研成果具有过多的情况组合，如无div标签但p标签+span标签
        # 单独div标签，单独p标签，有div标签等等组合
        # 所以这里考虑的是最综合的结果
        # 将所有的结果汇总到一起后得到一个列表，之后会对列表进行再处理
        if len(content) > 0:
            # 对于非列表类型的数据无法相加，因此给出if判断
            if type(content) == list:
                info = info + content
            else:
                info = info + list(content)

### 对上述所提到的科研成果以及自我介绍进行筛选拆分

In [30]:
# 对以上提取出的列表内容进行判断处理
# info中的内容是均来自于p以下所有span或strong以及其自身的文本内容
# div_span_text是属于div标签下的span标签内容
# div_text是属于div标签下的所有内容
# 因为其存在重复（即若存在div标签，那么div中的span会与p中的span内容重复），因此需要做出判断筛选
if (''.join(info) in ''.join(div_span_text) or ''.join(div_span_text) in ''.join(info)):
    # 如果p中内容在div中
    if ''.join(info) in ''.join(div_span_text):
        infos = div_span_text + div_text
    # 如果div中内容在p中
    elif ''.join(div_span_text) in ''.join(info):
        infos = info + div_text

   # 如果两者都不存在相互重复     
elif (''.join(info) not in ''.join(div_span_text) and ''.join(div_span_text) not in ''.join(info)):
    infos = info + div_span_text + div_text

# Sign作为标识判断用，如果已得到索引，那么False
# 而这里定义research_index和self_index是防止局部变量错误调用提示，中断程序
Sign1 = True; Sign2 = True
research_index = 0; self_index = 0
for index, item in enumerate(infos):
    # 以如下的关键词作为科研成果筛选标准
    if ('论文' in item or '主要成果' in item or '科研成果' in item or 'Major Research Publications' in item) and Sign1:
        research_index = index
        Sign1 = False
    # 同理如下的关键词作为自我简介的筛选
    if ('开设课程' in item or '个人简介' in item or 'Education' in item) and Sign2:
        self_index = index
        Sign2 = False

# 由于顺序可能存在错乱，需要进行大小判定
if self_index < research_index:
    Self_introduction = infos[self_index:research_index]
    Research = infos[research_index:]
else:
    Research = infos[research_index:self_index]
    Self_introduction = infos[self_index:]

Basic_info['个人简介'] = [''.join(Self_introduction)]
Basic_info['科研成果'] = [''.join(Research)]
# 将不同dict转换具有相同key的字典，便于后续转化为DataFrame
# 这里就用到了之前的sub_info，一方面是为了补充某些老师缺失的key，另一方面是为了使每个老师有一样的key
for item in sub_info:
    if item not in list(Basic_info.keys()):
        Basic_info[item] = ['无']

pd_info = pd.DataFrame(Basic_info, columns=['姓名', '性别','出生年月','政治面貌','毕业院校','毕业专业','最高学历','职务','职称','联系方式','个人简介','科研成果'])
display(HTML(pd_info.to_html()))

## 所有老师信息展示

### 定义函数

In [19]:
def get_info(url, symbol):
    '''
    参数解释
    url: 每个老师的链接
    symbol：由于硕导老师中存在外教，因此一些符号格式并不同
    '''
    r = requests.get(url, headers=headers).text
    html = etree.HTML(r)
    target = html.xpath('//div[@class="ne_main_R"]//p')
    div_text = html.xpath('//div[@class="ne_main_R"]//div[@class="jianjie_c"]/text()')
    div_span_text = html.xpath('//div[@class="ne_main_R"]//div[@class="jianjie_c"]//span/text()')
    Flag = 0
    info = []
    infos = []
    Basic_info = {}
    sub_info = ['职务','职称','联系方式','毕业专业','最高学历','政治面貌','毕业院校','出生年月']
    sub_dict = {'Name':'姓名','Sex':'性别','Graduated':'毕业院校','Duties':'职务',
                    'Email':'联系方式', 'Jobtitle':'职称','邮箱':'联系方式','电子邮箱':'联系方式'}
    for i in range(len(target)):
        tar = target[i]
        # 基本信息
        content1 = tar.xpath('.//strong/text()')
        content2 = tar.xpath('.//span/text()')
        content3 = tar.xpath('./text()')
        content = content1 + content2 + content3
        # Flag = 0 表示对基本信息的提取；依次递推1表示对个人简介的提取，2表示对研究成果的提取
        if Flag == 0:
            # 经过多次更改标签形式的爬取结果可知，所有老师的基本信息都位于上述3个Content的标签下
            # 具有一定的规则性，因此考虑对其细分
            # 由于得到的content是个列表，需要根据情况对其进行处理
            # 有些老师的内容分散在不同的标签下，因此content列表的大小对应着不同情况
            if len(content) == 0:
                continue
            
            # 三个以上
            # 例：['姓名', '：', 'xxx']或['毕业','院校', ':xx', 'xxx']
            elif len(content) > 2:
                # 列表转字符方便后续正则处理
                content = ''.join(content)
                if symbol == content[-1]:
                    # 这里的相加顺序是均具备这个规则，一般
                    content = content1 + content3 + content2
                    
                content = ''.join(content)
                try:
                    content1 = re.findall(r"(.+){}".format(symbol), content, re.DOTALL)[0]
                    content2 = re.findall(r"{}(.+)".format(symbol), content, re.DOTALL)[0]
                except:
                    print('ERROR',content)
            # 有两个
            # 例：['姓名：', 'xxx']或['毕业院校', ':xxxxx']
            elif len(content) == 2:
                content1 = content[0]
                content2 = content[1]
            #只有一个
            else:
                # \uxxx类型的出现
                try:
                    content1 = re.findall(r"(.+){}".format(symbol), content[0], re.DOTALL)
                except:
                    continue
                # 空Key
                if len(content1) == 0:
                    continue
                content1 = content1[0]
                try:
                    content2 = re.findall(r"{}(.+)".format(symbol), content[0], re.DOTALL)[0]
                except:
                    print('!Error', content1)
            ## 注意，如果json调完格式之后再此用正则，仍然会匹配出\u3000类文本
            content1 = content1.replace('\u3000','').replace('\u200b','').replace('\xa0','')
            content2 = content2.replace('\u3000','').replace('\u200b','').replace('\xa0','')
            
            if symbol in content1:
                content1 = (content1.replace(' ', ''))[:-1]
            
            if symbol in content2:
                content2 = (content2.replace(' ', ''))[1:]
                if content2 == '':
                    content2 = '无'
            # 联系方式(邮箱)转化成一样的key
            if re.match(r'[a-zA-Z]+', content1) or re.match(r'.*邮箱', content1.replace(' ','')):
                content1 = sub_dict[content1.replace(' ','')]
            
#            print(content1, symbol, content2)    
            Basic_info[content1.replace(' ','')] = content2
            # 联系方式，邮箱，职称
            if i >= 5:
                string = str(Basic_info.keys())
                if ('联系方式' in list(Basic_info.keys())[-1] and '称' in string) or ('箱' in list(Basic_info.keys())[-1] and '称' in string) or ('邮&nbsp' not in r and '联系方式' not in r and '称' in list(Basic_info.keys())[-1]):
                    Flag = 1
                if ('Email' in string and 'Duties' in string):
                    Flag = 1
        # 自我简介
        elif Flag == 1:
            # 由于自我简介以及科研成果具有过多的情况组合，如无div标签但p标签+span标签
            # 单独div标签，单独p标签，有div标签等等组合
            # 所以这里考虑的是最综合的结果
            # 将所有的结果汇总到一起后得到一个列表，之后会对列表进行再处理
            if len(content) > 0:
                # 对于非列表类型的数据无法相加，因此给出if判断
                if type(content) == list:
                    info = info + content
                else:
                    info = info + list(content)
    
    # 对以上提取出的列表内容进行判断处理
    # info中的内容是均来自于p以下所有span或strong以及其自身的文本内容
    # div_span_text是属于div标签下的span标签内容
    # div_text是属于div标签下的所有内容
    # 因为其存在重复（即若存在div标签，那么div中的span会与p中的span内容重复），因此需要做出判断筛选
    if (''.join(info) in ''.join(div_span_text) or ''.join(div_span_text) in ''.join(info)):
        # 如果p中内容在div中
        if ''.join(info) in ''.join(div_span_text):
            infos = div_span_text + div_text
        # 如果div中内容在p中
        elif ''.join(div_span_text) in ''.join(info):
            infos = info + div_text
         
       # 如果两者都不存在相互重复     
    elif (''.join(info) not in ''.join(div_span_text) and ''.join(div_span_text) not in ''.join(info)):
        infos = info + div_span_text + div_text
    
    # Sign作为标识判断用，如果已得到索引，那么False
    # 而这里定义research_index和self_index是防止局部变量错误调用提示，中断程序
    Sign1 = True; Sign2 = True
    research_index = 0; self_index = 0
    for index, item in enumerate(infos):
        # 以如下的关键词作为科研成果筛选标准
        if ('论文' in item or '主要成果' in item or '科研成果' in item or 'Major Research Publications' in item) and Sign1:
            research_index = index
            Sign1 = False
        # 同理如下的关键词作为自我简介的筛选
        if ('开设课程' in item or '个人简介' in item or 'Education' in item) and Sign2:
            self_index = index
            Sign2 = False
            
    # 由于顺序可能存在错乱，需要进行大小判定
    if self_index < research_index:
        Self_introduction = infos[self_index:research_index]
        Research = infos[research_index:]
    else:
        Research = infos[research_index:self_index]
        Self_introduction = infos[self_index:]
    
    Basic_info['个人简介'] = ''.join(Self_introduction)
    Basic_info['科研成果'] = ''.join(Research)
    # 将不同dict转换具有相同key的字典，便于后续转化为DataFrame
    for item in sub_info:
        if item not in list(Basic_info.keys()):
            Basic_info[item] = '无'

        
    return Basic_info

### 由于前述过程中调整了每个老师的key，因此在此合并打印输出

In [22]:
total_url = 'http://finance.jxufe.edu.cn/news-list-shuodao-{}.html'
r_text = requests.get(total_url.format(1), headers=headers).text
html = etree.HTML(r_text)
num = html.xpath('//div[@class="bd_listabc"]//p/span[@class="num"]/text()')[0]
page_num = int(re.findall(r".+/(\d)页", num, re.DOTALL)[0])
List_info = []
for i in range(1, page_num+1):
    if i >= 2:
        r_text = requests.get(total_url.format(i), headers=headers).text
        html = etree.HTML(r_text)
    urls = html.xpath('//div[@class="bd_listabc"]//li//div[@class="textlist"]/a/@href')
    for url in urls:
        symbol = '：'
        if url == 'http://finance.jxufe.edu.cn/news-show-3097.html':
            symbol = ':'
#         print('-'*10+'江西财经大学金融学院硕导'+'-'*10)
        info = get_info(url, symbol)
#         print('\n'*2)
        List_info.append(info)

    
pd_Info = pd.DataFrame(List_info, columns=['姓名', '性别','出生年月','政治面貌','毕业院校','毕业专业','最高学历','职务','职称','联系方式','个人简介','科研成果'])
display(HTML(pd_Info.to_html()))

###

### 一点总结